## Dependencies

In [2]:
# Confirmed needed dependencies
import pprint
import pandas as pd
import requests
import json

# Dependencies for geocoordinates generator
import sys
import random
import math
import gmplot

# Dependencies for conversion of coordinates to addresses
import geopy
from geopy.geocoders import Nominatim
import time

# Dependencies for Zillow data
from pyzillow.pyzillow import ZillowWrapper, GetDeepSearchResults, GetUpdatedPropertyDetails

# Dependency for Heat Mapper
import gmaps


# Add config.py file with the following variables and cooresponding Zillow API keys
from config import Zapi, Zapi01, Zapi02, Zapi03, Zapi04, Zapi05, Zapi06, Zapi07, Zapi08, Zapi09, Zapi10, Zapi11, Zapi12, Zapi13, Zapi14, Zapi15, Zapi16, Zapi17, Zapi18, Zapi19, Zapi20, Ztroy1, Ztroy2, Ztroy3, Zseth, Zseth2, Zkat, Zval, Zyuta
# from config import google_API_Key
# from config import census_API_Key

################# ONGOING EDITS TO REQUIREMENTS.MD #################
###### IF ANY ERRORS OCCUR RELATING TO MODULES OR CONFIG.PY #######
### REFER TO requirements.md TO ENSURE YOU ARE PROPERLY SETUP ####

## File inputs/outputs

In [ ]:
# These routes have changed and must be updated before using

masterDataCLEAN_csv = "./Data/masterDataCLEAN.csv"


randLatLon_csv = "./Data/randomLatLon.csv" 
addressList_csv = "./Data/addressList.csv"
masterData_csv = "./Data/masterData.csv"
masterDFIMPORTclean_csv = "./Data/masterDFIMPORTclean.csv"
masterData100_csv = "./Data/masterData100.csv"
masterData1000_csv = "./Data/masterData1000.csv"

## Helpful Functions

In [ ]:
#############################
##### VALERIE'S BLOCKS #####
###########################

# Funtion for reading CSV in as DataFrame
def csvDF(oldCSVfilepath):
    csvIN = pd.read_csv(oldCSVfilepath)
    DF = pd.DataFrame(csvIN)
    return DF

# Function for converting DataFrame to CSV
def DFcsv(dataframe, newCSVfilepath):
    dataframe.to_csv(newCSVfilepath, index=False, header=True)
    print(f"Successfully written to '{newCSVfilepath}'")
    
# Function for reading in csv, checking for headers, and appending if appropriate
def csvDFappend(oldCSVfilepath, newColumn):
    csvIN = pd.read_csv(oldCSVfilepath)
    DF = pd.DataFrame(csvIN)
    # Checking to ensure new header name does not match any current headers
    colNames = DF.columns
    for value in colNames:
        if value == newColumn:
            print("Cannot append column that matches an existing column name")
            return DF
    # Check to ensure length of newColumn matches length of current dataframe columns
    if len(newColumn) != len(DF):
        print("Cannot append column that is not the same length as existing dataframe")
        return DF
    # Append newColumn to Dataframe
    DF[newColumn] = newColumn
    return DF

## Geocoordinates of Austin

In [ ]:
##########################################
# this section written by troy bailey.   #
# enter uservariables below to determine #
# center location, radius of circle, and #
# number of geocoordinates to generate.  #
##########################################

In [ ]:
########################
#### USER VARIABLES ####
########################

x0 = 30.27444       #### Set center coordiantes in decimal degrees
y0 = -97.74028      #### initial coordiantes are location of Texas State Capitol Building

radius = 20         #### Set radius in miles

points = 40000        #### Set number of lat,lon points to generate

In [ ]:
# variables and inputs for coordinate calculations
lat_lon_list = []
radiusInDegrees=radius/69           
r = radiusInDegrees
points += 1

In [ ]:
# calculate each coordiante point and build a list of lat and lon
for i in range(1, points):
    u = float(random.uniform(0.0,1.0)) #random number for radius length
    v = float(random.uniform(0.0,1.0)) #random number for pi radians
    
    w = r * math.sqrt(u) #radius length
    t = 2 * math.pi * v  #radians
    x = w * math.cos(t)  #calculate x coord distance
    y = w * math.sin(t)  #calculate y coord distance
    
    xLat  = x + x0       #offset x by center x
    yLon = y + y0        #offset y by center y
    
    lat_lon_list.append([xLat,yLon])

# convert list to dataframe
lat_lon_df = pd.DataFrame(lat_lon_list, columns=['lat','lon'])

lat_lon_df.head()

len(lat_lon_df)

In [ ]:
# write a CSV file of coordinate points
lat_lon_df.to_csv(randLatLon_csv, index=False, header=True)

## Plot coordinate points on map


In [ ]:
# This cell by Troy
# This section will plot points on a Google map centered at centerPointLat and centerPointLon with a magnification of magFactor
# It assumes there is a dataframe with "lat" and "lon" columns
# The resulting map is saved to a file called 

lat_lon_df = pd.read_csv("./Data/Archived/randomLatLon.csv")
centerPointLat = 30.27444  #these are the coordinates of the Texas State Capitol building
centerPointLon = -97.74028 #these are the coordinates of the Texas State Capitol building
magnificationFactor = 10
pointColor = "red"
pointSize = 100
mapOutputFile = "randLatLonMap.html"
df = lat_lon_df

gmap = gmplot.GoogleMapPlotter(centerPointLat, centerPointLon, magnificationFactor)

gmap.scatter(df["lat"], df["lon"], pointColor, size=pointSize, marker=False)

gmap.draw("./Presentation/" + mapOutputFile)

len(df)

## Convert Coordinates to Residential Addresses

In [ ]:
#########################
##### Yuta's Blocks #####
#########################

##### Geopy Nominatim API #####
geopy.geocoders.options.default_user_agent = "ut-group-EPIC"

pp = pprint.PrettyPrinter(indent=4)

url = "https://nominatim.openstreetmap.org/reverse?"

In [ ]:
# Test API - Known Residential Address
params_1 = {
    "format": "jsonv2",
    "lat": 30.440777,
    "lon": -97.777048
}

print("===== Test Home Response:")
response = requests.get(url, params=params_1).json()
pp.pprint(response)
print("\n" + "="*60 + "\n")

In [ ]:
# Import CSV, put into DataFrame
latlon_df = pd.read_csv(randLatLon_csv)
latlon_df.head()

In [ ]:
# Put latitudes and longitudes into a zip object
lats = latlon_df.iloc[:, 0]
lons = latlon_df.iloc[:, 1]
lat_lons = []
lat_lons = zip(lats, lons)

In [ ]:
##### Loop Request API for Addresses / Append to lists #####
# Make sure to import time

query_url = "https://nominatim.openstreetmap.org/reverse?"

house_num = []
road = []
postcode = []
lat = []
lon = []
neighborhood = []

counter = 1
numRequests = latlon_df["lat"].count()
rSuccess = []
rFailure = []

print(f"Processing {numRequests} Requests...")

# Nominatim API Request

for lat_lon in lat_lons:
    params = {
        "format": "jsonv2",
        "lat": lat_lon[0],
        "lon": lat_lon[1]
    }

    time.sleep(1.1)
    response = requests.get(query_url, params=params).json()

    if response['type'] == 'house' or response['type'] == 'yes':
        lat.append(response['lat'])
        lon.append(response['lon'])
        
        try:
            postcode.append(response['address']['postcode'])
        except (KeyError, IndexError):
            postcode.append("NA")
        try:
            house_num.append(response['address']['house_number'])
        except (KeyError, IndexError):
            house_num.append("NA")
        try:
            road.append(response['address']['road'])
        except (KeyError, IndexError):
            road.append("NA")
        try:
            neighborhood.append(response['address']['neighbourhood'])
        except (KeyError, IndexError):
            neighborhood.append("NA")
        
        print(f"Processed Record {counter} of {numRequests}.")
        rSuccess.append(counter)
        counter += 1
        
    else:
        print(f"Wrong Type - Skipped Record {counter} of {numRequests}.")
        rFailure.append(counter)
        counter += 1
        
print(f"Finished Requests !!!")

In [ ]:
print("Request Results:")
print("Success #:" + str(len(rSuccess)))
print("Skipped #:" + str(len(rFailure)))

In [ ]:
# Create dataframe with addresses from API requests
address_df = pd.DataFrame({
    "house #": house_num,
    "street": road,
    "zipcode": postcode,
    "lat": lat,
    "lon": lon,
    "neighborhood": neighborhood,
})

# Clean up Dataframe Columns before output (Drop incomplete zipcodes, Highway streets, and Null house # or streets)
address_df = address_df[address_df['zipcode'].str.len() == 5]
address_df = address_df[address_df['zipcode'].apply(lambda x: len(str(x)) > 3)]
address_df = address_df[address_df['street'].str.contains("Highway") == False]
address_df = address_df[address_df['house #'].str.contains("NA") == False]
address_df = address_df[address_df['street'].str.contains("NA") == False]
address_df.dtypes

In [ ]:
# write a CSV file of addresses
address_df.to_csv(addressList_csv, index=False, header=True)

In [ ]:
# Map out CSV with gmplot

addressList_csv = "./Data/addressList.csv"

gmap = gmplot.GoogleMapPlotter(30.27444, -97.74028, 10)

gmap.scatter(addressList_csv["lat"], addressList_csv["lon"], 'red', size=20, marker=False)

gmap.draw("./Visuals/myaddressmap.html")

## Plot Addresses on a Map

In [ ]:
# This cell by Troy
# This section will plot points on a Google map centered at centerPointLat and centerPointLon with a magnification of magFactor
# It plots the addresses we have selected from the random Lat Lon points
# The resulting map is saved to a file called addressMap.html

address_df = pd.read_csv("./Data/Archived/addressList.csv")
centerPointLat = 30.27444  #these are the coordinates of the Texas State Capitol building
centerPointLon = -97.74028 #these are the coordinates of the Texas State Capitol building
magnificationFactor = 10
pointColor = "blue"
pointSize = 100
mapOutputFile = "addressMap.html"
df = address_df

gmap = gmplot.GoogleMapPlotter(centerPointLat, centerPointLon, magnificationFactor)

gmap.scatter(df["lat"], df["lon"], pointColor, size=pointSize, marker=False)

gmap.draw("./Presentation/" + mapOutputFile)

len(df)

## Zillow API Calls using Address and Zipcode

In [24]:
######################################################################################  RUN FOR FULL SAMPLE  ###################

#############################
##### VALERIE'S BLOCKS #####
###########################

# Funtion for reading CSV in as DataFrame
def csvDF(oldCSVfilepath):
    csvIN = pd.read_csv(oldCSVfilepath)
    DF = pd.DataFrame(csvIN)
    return DF

# Function for converting DataFrame to CSV
def DFcsv(dataframe, newCSVfilepath):
    dataframe.to_csv(newCSVfilepath, index=False, header=True)
    print(f"Successfully written to '{newCSVfilepath}'")
    
# Function for reading in csv, checking for headers, and appending if appropriate
def csvDFappend(oldCSVfilepath, newColumn):
    csvIN = pd.read_csv(oldCSVfilepath)
    DF = pd.DataFrame(csvIN)
    # Checking to ensure new header name does not match any current headers
    colNames = DF.columns
    for value in colNames:
        if value == newColumn:
            print("Cannot append column that matches an existing column name")
            return DF
    # Check to ensure length of newColumn matches length of current dataframe columns
    if len(newColumn) != len(DF):
        print("Cannot append column that is not the same length as existing dataframe")
        return DF
    # Append newColumn to Dataframe
    DF[newColumn] = newColumn
    return DF

In [4]:
######################################################################################  RUN FOR FULL SAMPLE  ###################

# Read in address list to run through Zillow API 
addressDF = csvDF("../data/Archived/addressList.csv")

In [5]:
######################################################################################  RUN FOR FULL SAMPLE  ###################

print(len(addressDF))
addressDF.head()

20177


house #           street  zipcode        lat        lon         neighborhood
0   11508        Carl Road    78747  30.110836 -97.750350                  NaN
1   11206  Lime Creek Road    78641  30.485701 -97.898313                  NaN
2    2905  Etta James Cove    78613  30.486673 -97.863239                  NaN
3     607       River Road    78734  30.344156 -97.928864                  NaN
4   15029  Donna Jane Loop    78660  30.438135 -97.656384  Spring Hill Village

In [6]:
######################################################################################  RUN FOR FULL SAMPLE  ###################

# Drop duplicates prior to running Zillow API call
addressDF = addressDF.drop_duplicates()
print(len(addressDF))

16706


In [7]:
######################################################################################  RUN FOR FULL SAMPLE  ###################

############### LOOPING FUNCTION FULLY OPERATIONAL ################
####### HOWEVER, ZILLOW ONLY ALLOWS 1000 API CALLS PER DAY #######

# Zillow API call function using address and zipcode
def zCall(API, index, address, zipcode):
    APIkey = API[index]
    zillow_data = ZillowWrapper(APIkey)
    deep_search_response = zillow_data.get_deep_search_results(address, zipcode)
    result = GetDeepSearchResults(deep_search_response)
    return result


# List containers for collected property data
zid = []
addresses = []
alats = []
alons = []
valuation = []
valChange = []
valRhigh = []
valRlow = []
sqft = []
lotsqft = []
yearBuilt = []
lastSold = []
lastPrice = []


# List of Zillow API keys to loop through due to daily API call limits
zAPIs = [Zapi, Zapi01, Zapi02, Zapi03, Zapi04, Zapi05, Zapi06, Zapi07, Zapi08, Zapi09, 
         Zapi10, Zapi11, Zapi12, Zapi13, Zapi14, Zapi15, Zapi16, Zapi17, Zapi18, Zapi19, 
         Zapi20, Ztroy1, Ztroy2, Ztroy3, Zseth, Zseth2, Zkat, Zval, Zyuta]
index = 0
    
for row, home in addressDF.iterrows():
    address = str(addressDF["house #"][row]) + " " + str(addressDF["street"][row])
    addresses.append(address)
    zipcode = addressDF["zipcode"][row]
    print(f"Processing {address}, {zipcode} (index {row}).")
    
    result = None
    try:
        try:
            result = zCall(zAPIs, index, address, zipcode)
            print(f"{row} Success!")
        except KeyError:  ### ERROR FOR API CALL LIMIT EXCEEDED ###
            print(f"KeyError has occurred for {address}, {zipcode} (index {row}).")
            index += 1
            print(f"Proceeding to API[{index}]")
            if index >= len(zAPIs):
                print(f"API[{index}] does not exist. Need more API keys to complete analysis.")
                break
            result = zCall(zAPIs, index, address, zipcode)

    except:
        print(f"No record found for {address}, {zipcode} (index {row}). Appending lists with null values")
        zid.append(None)
        alats.append(None)
        alons.append(None)
        valuation.append(None)
        valChange.append(None)
        valRhigh.append(None)
        valRlow.append(None)
        sqft.append(None)
        lotsqft.append(None)
        yearBuilt.append(None)
        lastSold.append(None)
        lastPrice.append(None)
        continue

    try:
        zillowID = result.zillow_id
        zid.append(zillowID)
    except:
        print(f"No zid found for {address}, {zipcode} (index {row}). Appending list with null values")
        zid.append(None)

    try:
        alat = result.latitude
        alats.append(alat)
    except:
        print(f"No alat found for {address}, {zipcode} (index {row}). Appending list with null values")
        alats.append(None)

    try:
        alon = result.longitude
        alons.append(alon)
    except:
        print(f"No alon found for {address}, {zipcode} (index {row}). Appending list with null values")
        alons.append(None)

    try:    
        val = int(result.zestimate_amount)
        valuation.append(val)
    except:
        print(f"No valuation found for {address}, {zipcode} (index {row}). Appending list with null values")
        valuation.append(None)
        
    try:    
        change = result.zestimate_value_change
        valChange.append(change)
    except:
        print(f"No valuation change found for {address}, {zipcode} (index {row}). Appending list with null values")
        valChange.append(None)
        
    try:    
        high = result.zestimate_valuation_range_high
        valRhigh.append(high)
    except:
        print(f"No valuation range high found for {address}, {zipcode} (index {row}). Appending list with null values")
        valRhigh.append(None)

    try:    
        low = result.zestimate_valuationRange_low
        valRlow.append(low)
    except:
        print(f"No valuation range low found for {address}, {zipcode} (index {row}). Appending list with null values")
        valRlow.append(None)
        
    try:
        zsqft = result.home_size
        sqft.append(zsqft)
    except:
        print(f"No sqft found for {address}, {zipcode} (index {row}). Appending list with null values")
        sqft.append(None)
        
    try:
        lot = result.property_size
        lotsqft.append(lot)
    except:
        print(f"No lot size for {address}, {zipcode} (index {row}). Appending list with null values")
        lotsqft.append(None)
        
    try:
        year = int(result.year_built)
        yearBuilt.append(year)
    except:
        print(f"No year built for {address}, {zipcode} (index {row}). Appending list with null values")
        yearBuilt.append(None)
        
    try:
        last = result.last_sold_date
        lastSold.append(last)
    except:
        print(f"No last sold date for {address}, {zipcode} (index {row}). Appending list with null values")
        lastSold.append(None)
        
    try:
        price = result.last_sold_price
        lastPrice.append(price)
    except:
        print(f"No last sold price for {address}, {zipcode} (index {row}). Appending list with null values")
        lastPrice.append(None)


Processing 11508 Carl Road, 78747 (index 0).
No record found for 11508 Carl Road, 78747 (index 0). Appending lists with null values
Processing 11206 Lime Creek Road, 78641 (index 1).
No record found for 11206 Lime Creek Road, 78641 (index 1). Appending lists with null values
Processing 2905 Etta James Cove, 78613 (index 2).
2 Success!
Processing 607 River Road, 78734 (index 3).
3 Success!
Processing 15029 Donna Jane Loop, 78660 (index 4).
4 Success!
Processing 12700 Johnson Lane, 78652 (index 5).
No record found for 12700 Johnson Lane, 78652 (index 5). Appending lists with null values
Processing 13805 Abrahamson Court, 78653 (index 6).
6 Success!
Processing 8113 West Gate Boulevard, 78745 (index 7).
7 Success!
Processing 4105 Aqua Verde Drive, 78746 (index 8).
8 Success!
Processing 10555 Maha Circle, 78747 (index 9).
9 Success!
Processing 4601 Fairview Drive, 78731 (index 10).
No record found for 4601 Fairview Drive, 78731 (index 10). Appending lists with null values
Processing 200 Hil

No record found for 15425 Farm-to-Market Road 973, 78653 (index 74). Appending lists with null values
Processing 13954 Murfin Road, 78734 (index 75).
No record found for 13954 Murfin Road, 78734 (index 75). Appending lists with null values
Processing 423 Pine Siskin Drive, 78610 (index 76).
No record found for 423 Pine Siskin Drive, 78610 (index 76). Appending lists with null values
Processing 740 Hillside Terrace Drive, 78610 (index 77).
No record found for 740 Hillside Terrace Drive, 78610 (index 77). Appending lists with null values
Processing 17408 Sleepy Hollow Drive, 78645 (index 78).
78 Success!
Processing 7250 Gilbert Road, 78653 (index 79).
No record found for 7250 Gilbert Road, 78653 (index 79). Appending lists with null values
Processing 11217 Crumley Ranch Road, 78736 (index 80).
No record found for 11217 Crumley Ranch Road, 78736 (index 80). Appending lists with null values
Processing 11006 Platt Lane, 78725 (index 81).
No record found for 11006 Platt Lane, 78725 (index 81

154 Success!
Processing 12196 Running Bird Lane, 78758 (index 155).
155 Success!
Processing 7705 Huddleston Lane, 78745 (index 156).
156 Success!
Processing 108 Duck Lake Drive, 78734 (index 157).
157 Success!
Processing 1902 Shadowbrook Circle, 78681 (index 158).
158 Success!
Processing 9642 Maha Loop Road, 78617 (index 159).
No record found for 9642 Maha Loop Road, 78617 (index 159). Appending lists with null values
Processing 7807 Callbram Lane, 78736 (index 160).
160 Success!
Processing 7101 Cherry Meadow Drive, 78745 (index 161).
161 Success!
Processing 11620 Shadow Creek Drive, 78653 (index 162).
162 Success!
Processing 8320 Adirondack Trail, 78759 (index 163).
163 Success!
Processing 12132 Parsons Road, 78653 (index 164).
164 Success!
Processing 10347 Signal Hill Road, 78737 (index 165).
No record found for 10347 Signal Hill Road, 78737 (index 165). Appending lists with null values
Processing 150 Reeves Lane, 78612 (index 166).
No record found for 150 Reeves Lane, 78612 (index 1

No record found for 3699 Ed Bluestein Boulevard, 78721 (index 243). Appending lists with null values
Processing 15874 Hokanson Road, 78617 (index 244).
No record found for 15874 Hokanson Road, 78617 (index 244). Appending lists with null values
Processing 905 West Howard Lane, 78728 (index 245).
245 Success!
Processing 8035 Jesse Bohls Drive, 78660 (index 246).
No record found for 8035 Jesse Bohls Drive, 78660 (index 246). Appending lists with null values
Processing 10000 Hillside North, 78736 (index 247).
247 Success!
Processing 425 Kingston Lacy Boulevard, 78660 (index 248).
No record found for 425 Kingston Lacy Boulevard, 78660 (index 248). Appending lists with null values
Processing 7050 East Ben White Boulevard, 78742 (index 249).
No record found for 7050 East Ben White Boulevard, 78742 (index 249). Appending lists with null values
Processing 3509 Kelly Lane, 78660 (index 250).
250 Success!
Processing 911 Meadows Drive North, 78758 (index 251).
251 Success!
Processing 16602 Deep M

320 Success!
Processing 19625 Cheyenne Valley Drive, 78664 (index 321).
321 Success!
Processing 2400 Gardenia Drive, 78727 (index 322).
322 Success!
No valuation found for 2400 Gardenia Drive, 78727 (index 322). Appending list with null values
Processing 4703 South Forest Drive, 78745 (index 323).
323 Success!
Processing 6802 Syracuse Cove, 78723 (index 324).
324 Success!
Processing 1842 Osprey Ridge Loop, 78645 (index 325).
No record found for 1842 Osprey Ridge Loop, 78645 (index 325). Appending lists with null values
Processing 11800 Dessau Road, 78753 (index 326).
326 Success!
Processing 7684 Lazy River Cove, 78730 (index 327).
No record found for 7684 Lazy River Cove, 78730 (index 327). Appending lists with null values
Processing 20400 Blake Manor Road, 78653 (index 328).
No record found for 20400 Blake Manor Road, 78653 (index 328). Appending lists with null values
Processing 1217 West Mary Street, 78704 (index 329).
329 Success!
No valuation found for 1217 West Mary Street, 78704

...

No record found for 16313 Greenwood Drive, 78617 (index 19749). Appending lists with null values
Processing 13105 Canyon View, 78641 (index 19750).
19750 Success!
Processing 11800 Garden Meadow Road, 78725 (index 19751).
19751 Success!
Processing 1778 Farm-to-Market Road 2001, 78610 (index 19752).
No record found for 1778 Farm-to-Market Road 2001, 78610 (index 19752). Appending lists with null values
Processing 1222 Tomahawk Trail, 78616 (index 19754).
No record found for 1222 Tomahawk Trail, 78616 (index 19754). Appending lists with null values
Processing 2907 Cameron Loop, 78745 (index 19755).
19755 Success!
No year built for 2907 Cameron Loop, 78745 (index 19755). Appending list with null values
Processing 1208 Springdale Road, 78723 (index 19758).
19758 Success!
No valuation found for 1208 Springdale Road, 78723 (index 19758). Appending list with null values
Processing 2383 Versailles Drive, 78613 (index 19760).
No record found for 2383 Versailles Drive, 78613 (index 19760). Append

19845 Success!
Processing 13414 Cedar Lime Road, 78641 (index 19846).
19846 Success!
Processing 10116 Old San Antonio Road, 78748 (index 19847).
No record found for 10116 Old San Antonio Road, 78748 (index 19847). Appending lists with null values
Processing 9958 Ranch to Market Road 967, 78610 (index 19848).
No record found for 9958 Ranch to Market Road 967, 78610 (index 19848). Appending lists with null values
Processing 3401 Govalle Avenue, 78702 (index 19849).
19849 Success!
Processing 810 Terrace Mountain Drive, 78746 (index 19850).
19850 Success!
Processing 10312 Kariba Cove, 78726 (index 19851).
19851 Success!
Processing 6403 Decker Lane, 78724 (index 19852).
No record found for 6403 Decker Lane, 78724 (index 19852). Appending lists with null values
Processing 838 Green Pastures Drive, 78640 (index 19853).
No record found for 838 Green Pastures Drive, 78640 (index 19853). Appending lists with null values
Processing 10503 Foundation Road, 78726 (index 19855).
19855 Success!
Proces

19938 Success!
Processing 329 Canterbury Drive, 78737 (index 19939).
No record found for 329 Canterbury Drive, 78737 (index 19939). Appending lists with null values
Processing 8900 Curlew Drive, 78748 (index 19942).
19942 Success!
Processing 1609 Lakecliff Hills Lane, 78732 (index 19943).
19943 Success!
Processing 9301 Bell Mountain Drive, 78730 (index 19944).
19944 Success!
Processing 4213 Hookbilled Kite Drive, 78738 (index 19945).
19945 Success!
Processing 141 Royal Way, 78737 (index 19946).
No record found for 141 Royal Way, 78737 (index 19946). Appending lists with null values
Processing 367 Bartlett Drive West, 78610 (index 19947).
No record found for 367 Bartlett Drive West, 78610 (index 19947). Appending lists with null values
Processing 12307 Los Indios Trail, 78729 (index 19948).
19948 Success!
No valuation found for 12307 Los Indios Trail, 78729 (index 19948). Appending list with null values
Processing 2718 Turnersville Road, 78610 (index 19950).
19950 Success!
Processing 84

No record found for 16899 West Whitestone Boulevard, 78613 (index 20050). Appending lists with null values
Processing 11129 Callanish Park Drive, 78750 (index 20051).
20051 Success!
Processing 8105 Mowinkle Drive, 78736 (index 20053).
20053 Success!
Processing 9601 Beck Circle, 78758 (index 20054).
No record found for 9601 Beck Circle, 78758 (index 20054). Appending lists with null values
Processing 10805 Oak View Drive, 78759 (index 20056).
20056 Success!
Processing 5304 Honey Dew Terrace, 78749 (index 20058).
20058 Success!
Processing 349 Escondido Drive, 78617 (index 20059).
No record found for 349 Escondido Drive, 78617 (index 20059). Appending lists with null values
Processing 1804 Rabb Road, 78704 (index 20060).
20060 Success!
Processing 7416 Elroy Road, 78617 (index 20061).
20061 Success!
No valuation found for 7416 Elroy Road, 78617 (index 20061). Appending list with null values
Processing 217 Bella Riva Drive, 78734 (index 20062).
20062 Success!
Processing 12521 Amherst Drive,

No record found for 18009 FM 973, 78653 (index 20149). Appending lists with null values
Processing 7201 Lochinvar Street, 78749 (index 20150).
No record found for 7201 Lochinvar Street, 78749 (index 20150). Appending lists with null values
Processing 8300 Seminary Ridge Drive, 78745 (index 20151).
20151 Success!
Processing 8010 Clinger Road, 78719 (index 20152).
No record found for 8010 Clinger Road, 78719 (index 20152). Appending lists with null values
Processing 4717 Camacho Street, 78723 (index 20153).
20153 Success!
Processing 3105 I 35 Frontage Road, 78741 (index 20154).
No record found for 3105 I 35 Frontage Road, 78741 (index 20154). Appending lists with null values
Processing 1100 Water Street, 78653 (index 20155).
No record found for 1100 Water Street, 78653 (index 20155). Appending lists with null values
Processing 12940 Latchwood Lane, 78753 (index 20156).
20156 Success!
Processing 59 Country Oaks Drive, 78610 (index 20157).
20157 Success!
No year built for 59 Country Oaks D

## Master Dataframe Creation

In [8]:
######################################################################################  RUN FOR FULL SAMPLE  ###################

# Checking to ensure lengths of lists are identical
print(len(zid))
print(len(addresses))
print(len(alats))
print(len(alons))
print(len(valuation))
print(len(valChange))
print(len(valRhigh))
print(len(valRlow))
print(len(sqft))
print(len(lotsqft))
print(len(yearBuilt))
print(len(lastSold))
print(len(lastPrice))

# Referring back to addressList_csv generated dataframe for relevant info
addressDF.head()
print(len(addressDF))

16706
16706
16706
16706
16706
16706
16706
16706
16706
16706
16706
16706
16706
16706


In [9]:
######################################################################################  RUN FOR FULL SAMPLE  ###################

masterDF = pd.DataFrame({
    "zid": zid,
    "address": addresses,
    "zipcode": addressDF["zipcode"],
    "alat": alats,
    "alon": alons,
    "valuation": valuation,
    "value_change": valChange,
    "value_range_high": valRhigh,
    "value_range_low": valRlow,
    "sqft": sqft,
#     "value_sqft": valsqft,
    "lot_sqft": lotsqft,
    "year_built": yearBuilt,
    "last_sold_date": lastSold,
    "last_sold_price": lastPrice,
})

print(len(masterDF))
masterDF.head(10)

16706


zid                   address  zipcode       alat        alon  \
0       None           11508 Carl Road    78747       None        None   
1       None     11206 Lime Creek Road    78641       None        None   
2   83820301      2905 Etta James Cove    78613   30.48666  -97.863306   
3  114405051            607 River Road    78734  30.344178  -97.928907   
4   60134868     15029 Donna Jane Loop    78660   30.43816  -97.656383   
5       None        12700 Johnson Lane    78652       None        None   
6   70354229    13805 Abrahamson Court    78653  30.360686  -97.473507   
7   29498621  8113 West Gate Boulevard    78745  30.197589  -97.828106   
8   29346558     4105 Aqua Verde Drive    78746  30.342889  -97.810038   
9  144352111         10555 Maha Circle    78747  30.107525  -97.698309   

   valuation value_change value_range_high value_range_low  sqft lot_sqft  \
0        NaN         None             None            None  None     None   
1        NaN         None             None            None  None     None   
2   381218.0          381           400279          362157  2395    11194   
3  1340505.0       -26046          1608606         1139429  4500    42383   
4   216662.0         1912           227495          205829  1745     4051   
5        NaN         None             None            None  None     None   
6   139455.0        -4722           179897          108775  1288   501114   
7   265041.0        -3015           283594          241187   940    12066   
8   658102.0        -9308           691007          625197  2383    21802   
9   264198.0         2091           290618          216642  1362   248410   

   year_built last_sold_date last_sold_price  
0         NaN           None            None  
1         NaN           None            None  
2      2008.0           None            None  
3      2012.0           None            None  
4      2002.0           None            None  
5         NaN           None            None  
6      1980.0           None            None  
7      1984.0           None            None  
8      1983.0           None            None  
9      1970.0           None            None

In [10]:
######################################################################################  RUN FOR FULL SAMPLE  ###################

# masterDFclean to csv
masterDF.to_csv("../data/zillowRaw.csv", index=False, header=True)
masterDF.head(30)

zid                         address  zipcode       alat        alon  \
0        None                 11508 Carl Road    78747       None        None   
1        None           11206 Lime Creek Road    78641       None        None   
2    83820301            2905 Etta James Cove    78613   30.48666  -97.863306   
3   114405051                  607 River Road    78734  30.344178  -97.928907   
4    60134868           15029 Donna Jane Loop    78660   30.43816  -97.656383   
5        None              12700 Johnson Lane    78652       None        None   
6    70354229          13805 Abrahamson Court    78653  30.360686  -97.473507   
7    29498621        8113 West Gate Boulevard    78745  30.197589  -97.828106   
8    29346558           4105 Aqua Verde Drive    78746  30.342889  -97.810038   
9   144352111               10555 Maha Circle    78747  30.107525  -97.698309   
10       None             4601 Fairview Drive    78731       None        None   
11       None      200 Hillside Terrace Drive    78610       None        None   
12   29440641             2109 Red Stone Lane    78727  30.418454   -97.69619   
13       None             1157 Brinkley Drive    78613       None        None   
14   29345444               9 Glen Rock Drive    78738  30.341187  -97.984049   
15   29613796            8333 Alvin High Lane    78729  30.460441  -97.761118   
16   29358809             5300 Valburn Circle    78731  30.374096  -97.775259   
17   29471589            11125 Maha Loop Road    78617  30.082419  -97.664366   
18   29352791               102 Javelin Drive    78734  30.360267  -97.998646   
19       None                 6401 1/2 RM 620    78730       None        None   
20       None       1601 Green Pastures Drive    78725       None        None   
21   64884422            7220 Cielo Azul Pass    78726   30.41662  -97.874616   
22   29417097           2000 Brentwood Street    78757  30.340507  -97.734626   
23   83820494  12220 Dwight Eisenhower Street    78653  30.354256  -97.526464   
24  144341633          1253 Dunlap Road South    78725   30.22287  -97.566622   
25       None          10746 Signal Hill Road    78737       None        None   
26       None          10802 Darden Hill Road    78619       None        None   
27       None            9408 Lime Creek Road    78641       None        None   
28   29329859                1518 Palma Plaza    78703  30.282597  -97.759718   
29   29458788               403 Academy Drive    78704   30.25157    -97.7444   

    valuation value_change value_range_high value_range_low  sqft lot_sqft  \
0         NaN         None             None            None  None     None   
1         NaN         None             None            None  None     None   
2    381218.0          381           400279          362157  2395    11194   
3   1340505.0       -26046          1608606         1139429  4500    42383   
4    216662.0         1912           227495          205829  1745     4051   
5         NaN         None             None            None  None     None   
6    139455.0        -4722           179897          108775  1288   501114   
7    265041.0        -3015           283594          241187   940    12066   
8    658102.0        -9308           691007          625197  2383    21802   
9    264198.0         2091           290618          216642  1362   248410   
10        NaN         None             None            None  None     None   
11        NaN         None             None            None  None     None   
12   250406.0       -11245           262926          237886  1359     7357   
13        NaN         None             None            None  None     None   
14   460645.0        -2983           483677          437613  2896    10802   
15   301375.0        -3682           316444          283292  1983     7840   
16   995707.0        31149          1055449          916050  4376    20456   
17   228432.0        10668           253560          187314  1960    90648   
18   371823.0   

## Zillow Data Cleaning

In [11]:
######################################################################################  RUN FOR FULL SAMPLE  ###################

zillowDF = csvDF("../data/zillowRaw.csv")
print(len(zillowDF))
zillowDF.head()

16706


zid                address  zipcode       alat       alon  \
0          NaN        11508 Carl Road    78747        NaN        NaN   
1          NaN  11206 Lime Creek Road    78641        NaN        NaN   
2   83820301.0   2905 Etta James Cove    78613  30.486660 -97.863306   
3  114405051.0         607 River Road    78734  30.344178 -97.928907   
4   60134868.0  15029 Donna Jane Loop    78660  30.438160 -97.656383   

   valuation  value_change  value_range_high  value_range_low    sqft  \
0        NaN           NaN               NaN              NaN     NaN   
1        NaN           NaN               NaN              NaN     NaN   
2   381218.0         381.0          400279.0         362157.0  2395.0   
3  1340505.0      -26046.0         1608606.0        1139429.0  4500.0   
4   216662.0        1912.0          227495.0         205829.0  1745.0   

   lot_sqft  year_built last_sold_date  last_sold_price  
0       NaN         NaN            NaN              NaN  
1       NaN         NaN            NaN              NaN  
2   11194.0      2008.0            NaN              NaN  
3   42383.0      2012.0            NaN              NaN  
4    4051.0      2002.0            NaN              NaN

In [12]:
######################################################################################  RUN FOR FULL SAMPLE  ###################

# DATA CLEANING #
# Dropping duplicates
masterDFdrops = zillowDF.drop_duplicates(subset=["zid"], keep="first")
print(len(masterDFdrops))
masterDFdrops.head()

9938


zid                 address  zipcode       alat       alon  \
0          NaN         11508 Carl Road    78747        NaN        NaN   
2   83820301.0    2905 Etta James Cove    78613  30.486660 -97.863306   
3  114405051.0          607 River Road    78734  30.344178 -97.928907   
4   60134868.0   15029 Donna Jane Loop    78660  30.438160 -97.656383   
6   70354229.0  13805 Abrahamson Court    78653  30.360686 -97.473507   

   valuation  value_change  value_range_high  value_range_low    sqft  \
0        NaN           NaN               NaN              NaN     NaN   
2   381218.0         381.0          400279.0         362157.0  2395.0   
3  1340505.0      -26046.0         1608606.0        1139429.0  4500.0   
4   216662.0        1912.0          227495.0         205829.0  1745.0   
6   139455.0       -4722.0          179897.0         108775.0  1288.0   

   lot_sqft  year_built last_sold_date  last_sold_price  
0       NaN         NaN            NaN              NaN  
2   11194.0      2008.0            NaN              NaN  
3   42383.0      2012.0            NaN              NaN  
4    4051.0      2002.0            NaN              NaN  
6  501114.0      1980.0            NaN              NaN

In [13]:
######################################################################################  RUN FOR FULL SAMPLE  ###################

# Cleaning out None values for "valuation"
masterDFdrops = masterDFdrops.dropna(how="any", subset=["valuation"])
print(len(masterDFdrops))
masterDFdrops.head()

8833


zid                   address  zipcode       alat       alon  \
2   83820301.0      2905 Etta James Cove    78613  30.486660 -97.863306   
3  114405051.0            607 River Road    78734  30.344178 -97.928907   
4   60134868.0     15029 Donna Jane Loop    78660  30.438160 -97.656383   
6   70354229.0    13805 Abrahamson Court    78653  30.360686 -97.473507   
7   29498621.0  8113 West Gate Boulevard    78745  30.197589 -97.828106   

   valuation  value_change  value_range_high  value_range_low    sqft  \
2   381218.0         381.0          400279.0         362157.0  2395.0   
3  1340505.0      -26046.0         1608606.0        1139429.0  4500.0   
4   216662.0        1912.0          227495.0         205829.0  1745.0   
6   139455.0       -4722.0          179897.0         108775.0  1288.0   
7   265041.0       -3015.0          283594.0         241187.0   940.0   

   lot_sqft  year_built last_sold_date  last_sold_price  
2   11194.0      2008.0            NaN              NaN  
3   42383.0      2012.0            NaN              NaN  
4    4051.0      2002.0            NaN              NaN  
6  501114.0      1980.0            NaN              NaN  
7   12066.0      1984.0            NaN              NaN

In [14]:
######################################################################################  RUN FOR FULL SAMPLE  ###################

# Cleaning out None values for "sqft" 
masterDFdrops = masterDFdrops.dropna(how="any", subset=["sqft"])
print(len(masterDFdrops))
masterDFdrops.head()

8738


zid                   address  zipcode       alat       alon  \
2   83820301.0      2905 Etta James Cove    78613  30.486660 -97.863306   
3  114405051.0            607 River Road    78734  30.344178 -97.928907   
4   60134868.0     15029 Donna Jane Loop    78660  30.438160 -97.656383   
6   70354229.0    13805 Abrahamson Court    78653  30.360686 -97.473507   
7   29498621.0  8113 West Gate Boulevard    78745  30.197589 -97.828106   

   valuation  value_change  value_range_high  value_range_low    sqft  \
2   381218.0         381.0          400279.0         362157.0  2395.0   
3  1340505.0      -26046.0         1608606.0        1139429.0  4500.0   
4   216662.0        1912.0          227495.0         205829.0  1745.0   
6   139455.0       -4722.0          179897.0         108775.0  1288.0   
7   265041.0       -3015.0          283594.0         241187.0   940.0   

   lot_sqft  year_built last_sold_date  last_sold_price  
2   11194.0      2008.0            NaN              NaN  
3   42383.0      2012.0            NaN              NaN  
4    4051.0      2002.0            NaN              NaN  
6  501114.0      1980.0            NaN              NaN  
7   12066.0      1984.0            NaN              NaN

### Calculate Value per Sqft

In [15]:
######################################################################################  RUN FOR FULL SAMPLE  ###################

# Calculate "value sqft" after None value rows removed for "valuation" and "sqft"

valsqft = []
for row, value in masterDFdrops.iterrows():
    try:
        vsqft = round((masterDFdrops["valuation"][row] / masterDFdrops["sqft"][row]), 2)
        valsqft.append(vsqft)
    except: ### THIS ERROR SHOULD NO LONGER PRINT BECAUSE NONE VALUES WERE PREVIOUSLY REMOVED
        print("Cannot perform math with NoneType")
        valsqft.append(None)

In [16]:
######################################################################################  RUN FOR FULL SAMPLE  ###################

# Checking to ensure lists are appropriate lengths
print(len(masterDFdrops))
print(len(valsqft))

8738
8738


In [17]:
######################################################################################  RUN FOR FULL SAMPLE  ###################

# Adding "value sqft" column
masterDFdrops["value_sqft"] = valsqft

# Reordering columns
masterDFdrops = masterDFdrops[['zid', 'address', 'zipcode', 'alat', 'alon', 'valuation', 'value_change', 'value_range_high',
                               'value_range_low', 'sqft', 'value_sqft', 'lot_sqft', 'year_built', 'last_sold_date', 
                               'last_sold_price']]
#                                , 'tractCode', 'countyFips', 'stateFips', 'commuteTime']]
masterDFdrops.head()

zid                   address  zipcode       alat       alon  \
2   83820301.0      2905 Etta James Cove    78613  30.486660 -97.863306   
3  114405051.0            607 River Road    78734  30.344178 -97.928907   
4   60134868.0     15029 Donna Jane Loop    78660  30.438160 -97.656383   
6   70354229.0    13805 Abrahamson Court    78653  30.360686 -97.473507   
7   29498621.0  8113 West Gate Boulevard    78745  30.197589 -97.828106   

   valuation  value_change  value_range_high  value_range_low    sqft  \
2   381218.0         381.0          400279.0         362157.0  2395.0   
3  1340505.0      -26046.0         1608606.0        1139429.0  4500.0   
4   216662.0        1912.0          227495.0         205829.0  1745.0   
6   139455.0       -4722.0          179897.0         108775.0  1288.0   
7   265041.0       -3015.0          283594.0         241187.0   940.0   

   value_sqft  lot_sqft  year_built last_sold_date  last_sold_price  
2      159.17   11194.0      2008.0            NaN              NaN  
3      297.89   42383.0      2012.0            NaN              NaN  
4      124.16    4051.0      2002.0            NaN              NaN  
6      108.27  501114.0      1980.0            NaN              NaN  
7      281.96   12066.0      1984.0            NaN              NaN

In [18]:
######################################################################################  RUN FOR FULL SAMPLE  ###################

# Checking high and low values with sort
masterDFdrops.sort_values(by="value_sqft", ascending=False)

zid                     address  zipcode       alat  \
7670   7.035247e+07  816 Lakewood Hills Terrace    78732  30.354888   
12464  6.260526e+07      16525 Rocky Ridge Road    78734  30.419540   
8159   1.442403e+08      15311 Decker Lake Road    78724  30.269981   
7473   1.449487e+08      4815 Rollingwood Drive    78746  30.274863   
7657   8.382454e+07       9601 Sandstone Street    78737  30.219186   
16194  6.477482e+07        16701 Red Wagon Lane    78641  30.493407   
4317   1.105367e+08   16900 Sleepy Hollow Drive    78645  30.407982   
8786   8.010405e+07    18852 Hidden Ridge Place    78645  30.456624   
3627   1.119701e+08        13401 Elm Grove Road    78610  30.038507   
14576  2.938100e+07        16400 Red Wagon Lane    78641  30.497639   
2540   1.258078e+08      14535 Pocohontas Trail    78641  30.428190   
13278  8.009797e+07      11301 Midmorning Drive    78737  30.202228   
13036  6.464234e+07           11504 Turtle Lane    78726  30.445901   
11106  7.033206e+07          2709 Benevento Way    78613  30.460566   
12652  8.382794e+07   13505 Bullick Hollow Road    78732  30.430459   
8838   1.105371e+08          11649 Johnson Road    78641  30.493197   
13295  1.258084e+08      19500 Blake Manor Road    78653  30.283120   
12937  1.258043e+08            8704 Linden Road    78617  30.127799   
1596   2.936471e+07   3400 Rainbow Hollow Drive    78645  30.406162   
9682   2.419301e+08           10917 Hamann Lane    78653  30.438709   
12203  2.936470e+07        3506 Lakeview Avenue    78645  30.407023   
8399   8.954756e+07     15700 Forest Glenn Cove    78617  30.147515   
6546   1.442914e+08          15605 Schmidt Lane    78653  30.390145   
583    2.947071e+07            7703 Linden Road    78617  30.145983   
4660   6.260530e+07         8108 Bernard Street    78641  30.452811   
4907   1.456524e+08      13705 Fuchs Grove Road    78653  30.370924   
12398  2.139071e+09  7321 Lookout Bluff Terrace    78735  30.242986   
823    2.947190e+07        13514 Elm Grove Road    78610  30.037064   
8282   2.947076e+07       16411 Fagerquist Road    78617  30.136968   
355    5.829795e+07       16001 Flint Rock Road    78738  30.332457   
...             ...                         ...      ...        ...   
14638  8.381488e+07          101 Webberwood Way    78621  30.240464   
9975   2.954898e+07              1 Edville Lane    78664  30.484114   
10772  2.944861e+07           801 Runners Ridge    78660  30.438336   
4887   2.947173e+07        7107 Appaloosa Court    78610  30.061478   
167    2.947166e+07            7100 Verde Court    78610  30.063327   
5586   2.939350e+07           8908 Ingrid Drive    78621  30.281110   
7094   2.939708e+07          9100 Tristam Drive    78621  30.284391   
14629  7.033457e+07      200 Boone Valley Drive    78660  30.490050   
13254  8.438520e+07       183 Legend Oaks Drive    78616  30.068207   
11779  2.940478e+07         7503 Northview Lane    78724  30.307623   
939    2.940777e+07      6910 Breezy Hill Drive    78724  30.309464   
7464   1.456528e+08          11815 Cameron Road    78754  30.359179   
5636   8.438068e+07              8310 Wolf Lane    78617  30.133604   
7363   5.829720e+07            1229 Faber Drive    78682  30.478546   
13961  2.144429e+08         223 Lazy River Lane    78621  30.216599   
12970  8.437032e+07         115 Rock Mont Drive    78617  30.131596   
12322  8.382504e+07    17708 Regatta View Drive    78645  30.449451   
3057   6.476815e+07                12509 FM 812    78719  30.130599   
11901  8.438516e+07              225 Stork Road    78617  30.094400   
12726  8.437047e+07         160 Edge Rock Drive    78617  30.131987   
7490   6.478256e+07     12001 Jim Bridger Drive    78737  30.199623   
2473   8.063597e+07    225 Arabian Stallion Run    78616  30.032360   
12326  8.438514e+07          194 Camino del Sol    78617  30.093292   
12971  8.437962e+07          113 Willie May Way    78621  30.228130   
5142   8.437615e+07       167 Stony Cree

In [19]:
######################################################################################  RUN FOR FULL SAMPLE  ###################

# Function for finding and dropping rows with nonsense values (e.g. valuation > $10,000,000)
def dropNonsense(dataframe, columnName, minVal, maxVal):
    dropIndices = []
    for index, row in dataframe.iterrows():
        val = dataframe[columnName][index]
        if (maxVal is not None) and (val > maxVal) or (minVal is not None) and (val < minVal):
            dropIndices.append(index)
    return dataframe.drop(index=dropIndices)

In [20]:
######################################################################################  RUN FOR FULL SAMPLE  ###################

# Establish reasonable values for columns
reasonableVals = [
    ("valuation", 20000, 10000000),
    ("sqft", 500, 10000),
    ("value_sqft", 0, 1500)
]

# Loop through dataframe to drop nonsense data
masterDFdrops = masterDFdrops
for entry in reasonableVals:
    masterDFdrops = dropNonsense(masterDFdrops, entry[0], entry[1], entry[2])

# Confirm count
print(len(masterDFdrops))

8591


In [26]:
masterDFdrops.to_csv("../data/zillowClean.csv", index=False, header=True)


In [ ]:
######################################################################################  RUN FOR FULL SAMPLE  ###################

# Save to file
DFcsv(masterDFdrops, "..data/zillowClean.csv")

### Merging Master Data with Commute Times

In [ ]:
commuteDF = csvDF("./Data/masterData.csv")
commuteDF.head()
print(len(commuteDF))
print(len(masterDFcleaning))
print("Commute")
print(commuteDF.dtypes)
print("Master")
print(masterDFcleaning.dtypes)
commuteDF.head()


In [ ]:
MASTERdf = pd.merge(masterDFcleaning, 
                    commuteDF[['tractCode', 'countyFips', 'stateFips', 'commuteTime']], 
                    how="left",
                    on='Zillow ID')

In [ ]:
print(len(MASTERdf))
MASTERdf.head()

## Plot Zillow Matched Addresses on a Map

In [ ]:
# This cell by Troy
# This section will plot points on a Google map centered at centerPointLat and centerPointLon with a magnification of magFactor
# It plots the Zillow addresses we have matched from our randomly selected 
# The resulting map is saved to a file called addressMap.html

masterData_df = pd.read_csv("./Data/masterDataCLEAN.csv")
centerPointLat = 30.27444  #these are the coordinates of the Texas State Capitol building
centerPointLon = -97.74028 #these are the coordinates of the Texas State Capitol building
magnificationFactor = 10
pointColor = "green"
pointSize = 100
mapOutputFile = "masterDataMap.html"
df = masterData_df

gmap = gmplot.GoogleMapPlotter(centerPointLat, centerPointLon, magnificationFactor)

gmap.scatter(df["alat"], df["alon"], pointColor, size=pointSize, marker=False)

gmap.draw("./Presentation/" + mapOutputFile)

len(df)

## Crime Data

In [47]:
crimeDF = csvDF("../data/Archived/annualCrimeData2016.csv")
crimeDF.columns
print(len(crimeDF))

37461


In [43]:
# Convert latitude and longitude to valid values
b = [3067322.0, 3114957.0, 3129181.0]
a = 3067322.0
a /= 100000
print(a)

for coord in b:
    coord /= 100000
    print(coord)

30.67322
30.67322
31.14957
31.29181


In [49]:
crimeDFdrops = crimeDF.dropna(how="any", subset=["GO X Coordinate"])
print(len(crimeDFdrops))

36594


In [50]:
crimeDFdrops = crimeDFdrops.dropna(how="any", subset=["GO Y Coordinate"])
print(len(crimeDFdrops))

36594


In [52]:
# Convert latitude and longitude to valid values
lats = crimeDFdrops['GO X Coordinate']
clats = []

for coord in lats:
    coord /= 100000
    clats.append(coord)
    
# Confirm length of list    
print(len(clats))

36594


In [53]:
# Convert latitude and longitude to valid values
lons = crimeDFdrops['GO Y Coordinate']
clons = []

for coord in lons:
    coord /= 100000
    clons.append(coord)
    
# Confirm length of list    
print(len(clons))

36594


In [63]:
# Drop previous coordinate columns
# crimeDFdrops = crimeDFdrops.drop(['GO X Coordinate', 'GO Y Coordinate'], axis=1)

print(crimeDFdrops.columns)
crimeDFdrops.head()

Index(['GO Primary Key', 'Council District', 'GO Highest Offense Desc',
       'Highest NIBRS/UCR Offense Description', 'GO Report Date',
       'GO Location', 'Clearance Status', 'Clearance Date', 'GO District',
       'GO Location Zip', 'GO Census Tract', 'Latitude', 'Longitude'],
      dtype='object')


GO Primary Key  Council District         GO Highest Offense Desc  \
0     201610188.0               8.0  AGG ASLT ENHANC STRANGL/SUFFOC   
1     201610643.0               9.0  THEFT                            
2     201610892.0               4.0  AGG ROBBERY/DEADLY WEAPON        
3     201610893.0               9.0  THEFT                            
5     201611148.0               1.0  DEADLY CONDUCT                   

  Highest NIBRS/UCR Offense Description GO Report Date          GO Location  \
0                           Agg Assault      01-Jan-16         8600 W SH 71   
1                                 Theft      01-Jan-16         219 E 6TH ST   
2                               Robbery      01-Jan-16  701 W LONGSPUR BLVD   
3                                 Theft      01-Jan-16      404 COLORADO ST   
5                           Agg Assault      01-Jan-16         8002 TAPO LN   

  Clearance Status Clearance Date GO District  GO Location Zip  \
0                C      12-Jan-16           D          78735.0   
1                C      04-Jan-16           G          78701.0   
2                N      03-May-16           E          78753.0   
3                N      22-Jan-16           G          78701.0   
5                N      08-Jan-16           C          78724.0   

   GO Census Tract  Latitude  Longitude  
0            19.08  30.67322  100.62796  
1            11.00  31.14957  100.70462  
2            18.23  31.29181  101.06923  
3            11.00  31.13643  100.70357  
5            22.08  31.46947  100.77985

In [58]:
# Append adjusted coordinate columns
crimeDFdrops["Latitude"] = clats
crimeDFdrops["Longitude"] = clons
crimeDFdrops.head()

GO Primary Key  Council District         GO Highest Offense Desc  \
0     201610188.0               8.0  AGG ASLT ENHANC STRANGL/SUFFOC   
1     201610643.0               9.0  THEFT                            
2     201610892.0               4.0  AGG ROBBERY/DEADLY WEAPON        
3     201610893.0               9.0  THEFT                            
5     201611148.0               1.0  DEADLY CONDUCT                   

  Highest NIBRS/UCR Offense Description GO Report Date          GO Location  \
0                           Agg Assault      01-Jan-16         8600 W SH 71   
1                                 Theft      01-Jan-16         219 E 6TH ST   
2                               Robbery      01-Jan-16  701 W LONGSPUR BLVD   
3                                 Theft      01-Jan-16      404 COLORADO ST   
5                           Agg Assault      01-Jan-16         8002 TAPO LN   

  Clearance Status Clearance Date GO District  GO Location Zip  \
0                C      12-Jan-16           D          78735.0   
1                C      04-Jan-16           G          78701.0   
2                N      03-May-16           E          78753.0   
3                N      22-Jan-16           G          78701.0   
5                N      08-Jan-16           C          78724.0   

   GO Census Tract  Latitude  Longitude  
0            19.08  30.67322  100.62796  
1            11.00  31.14957  100.70462  
2            18.23  31.29181  101.06923  
3            11.00  31.13643  100.70357  
5            22.08  31.46947  100.77985

In [64]:
crimeDFdrops['Highest NIBRS/UCR Offense Description'].nunique()

6

In [67]:
crimeDFsorted = crimeDFdrops.sort_values('Highest NIBRS/UCR Offense Description')
crimeDFsorted.head()

GO Primary Key  Council District         GO Highest Offense Desc  \
0        2.016102e+08               8.0  AGG ASLT ENHANC STRANGL/SUFFOC   
23735    2.016233e+10               2.0  AGG ASSAULT                      
23670    2.016232e+10               3.0  AGG ASSAULT                      
23643    2.016232e+10               2.0  AGG ASSAULT                      
23578    2.016231e+10               2.0  AGG ASLT STRANGLE/SUFFOCATE      

      Highest NIBRS/UCR Offense Description GO Report Date  \
0                               Agg Assault      01-Jan-16   
23735                           Agg Assault      20-Aug-16   
23670                           Agg Assault      19-Aug-16   
23643                           Agg Assault      19-Aug-16   
23578                           Agg Assault      18-Aug-16   

                  GO Location Clearance Status Clearance Date GO District  \
0                8600 W SH 71                C      12-Jan-16           D   
23735    5015 S IH 35 SVRD NB                C      21-Aug-16           F   
23670     4501 E RIVERSIDE DR                C      23-Aug-16           H   
23643      420 W SLAUGHTER LN                N      23-Aug-16           F   
23578  1402 TURTLE CREEK BLVD                C      19-Aug-16           F   

       GO Location Zip  GO Census Tract  Latitude  Longitude  
0              78735.0            19.08  30.67322  100.62796  
23735          78744.0            24.11  31.09951  100.47540  
23670          78741.0            23.14  31.21153  100.58007  
23643          78748.0            24.21  30.97944  100.35482  
23578          78745.0            24.09  30.98723  100.48509

In [68]:
crimeDFsorted.to_csv("../data/crimeData.csv", index=False, header=True)

## School Data

In [ ]:
# Seth's section

##  Commute Time Data

In [27]:
######################################################################################  RUN FOR FULL SAMPLE  ###################

# Troy's section

# This section reads the masterData csv file and uses the lat lon coordinates to get the us census tract code for that address
# It then uses the tract code to access the average commute times reported for that tract


# Load in data frame from file with lat and lon
masterData_df = csvDF("../data/zillowClean.csv")


lats = masterData_df['alat']
lons = masterData_df['alon']

# Set up arrays for new data
tractCodeList = []
countyFipsList = []
stateFipsList = []


# Use us census API to get state fips, county fips, and tract code for all addr in dataframe
for lat, lon in zip(lats,lons):
    print("getting data for " + str(lat) + str(lon))
    targetUrl = "https://geocoding.geo.census.gov/geocoder/geographies/coordinates?x=" + str(lon) + "&y=" + str(lat) + "&benchmark=Public_AR_Census2010&vintage=Census2010_Census2010&layers=14&format=json"
    results = requests.get(targetUrl).json()
#     print(results)
    tractCodeList.append(results["result"]["geographies"]["Census Blocks"][0]["TRACT"])
    countyFipsList.append(results["result"]["geographies"]["Census Blocks"][0]["COUNTY"])
    stateFipsList.append(results["result"]["geographies"]["Census Blocks"][0]["STATE"])
    
# Load new data into masterData
masterData_df["tractCode"] = tractCodeList
masterData_df["countyFips"] = countyFipsList
masterData_df["stateFips"] = stateFipsList

masterData_df.head()

getting data for 30.48666-97.863306
{'result': {'input': {'location': {'x': -97.863306, 'y': 30.48666}, 'vintage': {'isDefault': True, 'vintageName': 'Census2010_Census2010', 'vintageDescription': 'Census2010 Vintage - Census2010 Benchmark', 'id': '910'}, 'benchmark': {'isDefault': False, 'benchmarkName': 'Public_AR_Census2010', 'benchmarkDescription': 'Public Address Ranges - Census 2010 Benchmark', 'id': '9'}}, 'geographies': {'Census Blocks': [{'BLKGRP': '2', 'UR': '', 'OID': 210403962088010, 'FUNCSTAT': 'S', 'STATE': '48', 'AREAWATER': 0, 'NAME': 'Block 2025', 'SUFFIX': '', 'LSADC': 'BK', 'CENTLON': '-097.8709596', 'HU100': 83, 'LWBLKTYP': 'L', 'BLOCK': '2025', 'BASENAME': '2025', 'INTPTLAT': '+30.4760398', 'POP100': 254, 'MTFCC': 'G5040', 'COUNTY': '453', 'GEOID': '484530017652025', 'CENTLAT': '+30.4760398', 'INTPTLON': '-097.8709596', 'AREALAND': 5636507, 'OBJECTID': 9891103, 'TRACT': '001765'}]}}}
getting data for 30.344178000000007-97.928907
{'result': {'geographies': {'Census 

{'result': {'input': {'location': {'x': -97.761118, 'y': 30.460441}, 'vintage': {'isDefault': True, 'vintageName': 'Census2010_Census2010', 'vintageDescription': 'Census2010 Vintage - Census2010 Benchmark', 'id': '910'}, 'benchmark': {'isDefault': False, 'benchmarkName': 'Public_AR_Census2010', 'benchmarkDescription': 'Public Address Ranges - Census 2010 Benchmark', 'id': '9'}}, 'geographies': {'Census Blocks': [{'BLKGRP': '1', 'UR': '', 'OID': 210403968480695, 'FUNCSTAT': 'S', 'STATE': '48', 'AREAWATER': 439, 'NAME': 'Block 1004', 'SUFFIX': '', 'LSADC': 'BK', 'CENTLON': '-097.7581960', 'HU100': 83, 'LWBLKTYP': 'B', 'BLOCK': '1004', 'BASENAME': '1004', 'INTPTLAT': '+30.4613685', 'POP100': 196, 'MTFCC': 'G5040', 'COUNTY': '491', 'GEOID': '484910204111004', 'CENTLAT': '+30.4613746', 'INTPTLON': '-097.7581945', 'AREALAND': 205887, 'OBJECTID': 9953437, 'TRACT': '020411'}]}}}
getting data for 30.374096-97.775259
{'result': {'geographies': {'Census Blocks': [{'BLKGRP': '4', 'UR': '', 'OID': 

{'result': {'input': {'location': {'x': -97.790929, 'y': 30.520886}, 'vintage': {'isDefault': True, 'vintageName': 'Census2010_Census2010', 'vintageDescription': 'Census2010 Vintage - Census2010 Benchmark', 'id': '910'}, 'benchmark': {'isDefault': False, 'benchmarkName': 'Public_AR_Census2010', 'benchmarkDescription': 'Public Address Ranges - Census 2010 Benchmark', 'id': '9'}}, 'geographies': {'Census Blocks': [{'BLKGRP': '1', 'UR': '', 'OID': 210403968486172, 'FUNCSTAT': 'S', 'STATE': '48', 'AREAWATER': 1504, 'NAME': 'Block 1004', 'SUFFIX': '', 'LSADC': 'BK', 'CENTLON': '-097.7868691', 'HU100': 56, 'LWBLKTYP': 'B', 'BLOCK': '1004', 'BASENAME': '1004', 'INTPTLAT': '+30.5209103', 'POP100': 201, 'MTFCC': 'G5040', 'COUNTY': '491', 'GEOID': '484910203171004', 'CENTLAT': '+30.5194304', 'INTPTLON': '-097.7884187', 'AREALAND': 827321, 'OBJECTID': 9949102, 'TRACT': '020317'}]}}}
getting data for 30.167892-97.827473
{'result': {'geographies': {'Census Blocks': [{'BLKGRP': '2', 'UR': '', 'OID':

{'result': {'geographies': {'Census Blocks': [{'BLKGRP': '1', 'UR': '', 'OID': 210403968482290, 'FUNCSTAT': 'S', 'STATE': '48', 'AREAWATER': 0, 'NAME': 'Block 1022', 'SUFFIX': '', 'LSADC': 'BK', 'CENTLON': '-097.6438041', 'HU100': 85, 'LWBLKTYP': 'L', 'BLOCK': '1022', 'BASENAME': '1022', 'INTPTLAT': '+30.5248508', 'POP100': 229, 'MTFCC': 'G5040', 'COUNTY': '491', 'GEOID': '484910215081022', 'CENTLAT': '+30.5248508', 'INTPTLON': '-097.6438041', 'AREALAND': 546060, 'OBJECTID': 9946132, 'TRACT': '021508'}]}, 'input': {'location': {'x': -97.642224, 'y': 30.526467}, 'benchmark': {'benchmarkDescription': 'Public Address Ranges - Census 2010 Benchmark', 'benchmarkName': 'Public_AR_Census2010', 'isDefault': False, 'id': '9'}, 'vintage': {'vintageName': 'Census2010_Census2010', 'vintageDescription': 'Census2010 Vintage - Census2010 Benchmark', 'isDefault': True, 'id': '910'}}}}
getting data for 30.428063-97.800195
{'result': {'geographies': {'Census Blocks': [{'BLKGRP': '3', 'UR': '', 'OID': 21

{'result': {'input': {'location': {'x': -97.749343, 'y': 30.196212}, 'vintage': {'isDefault': True, 'vintageName': 'Census2010_Census2010', 'vintageDescription': 'Census2010 Vintage - Census2010 Benchmark', 'id': '910'}, 'benchmark': {'isDefault': False, 'benchmarkName': 'Public_AR_Census2010', 'benchmarkDescription': 'Public Address Ranges - Census 2010 Benchmark', 'id': '9'}}, 'geographies': {'Census Blocks': [{'BLKGRP': '3', 'UR': '', 'OID': 210403962094074, 'FUNCSTAT': 'S', 'STATE': '48', 'AREAWATER': 0, 'NAME': 'Block 3004', 'SUFFIX': '', 'LSADC': 'BK', 'CENTLON': '-097.7501420', 'HU100': 44, 'LWBLKTYP': 'L', 'BLOCK': '3004', 'BASENAME': '3004', 'INTPTLAT': '+30.1960013', 'POP100': 197, 'MTFCC': 'G5040', 'COUNTY': '453', 'GEOID': '484530024113004', 'CENTLAT': '+30.1960013', 'INTPTLON': '-097.7501420', 'AREALAND': 44150, 'OBJECTID': 9877805, 'TRACT': '002411'}]}}}
getting data for 30.230108-97.873572
{'result': {'geographies': {'Census Blocks': [{'BLKGRP': '1', 'UR': '', 'OID': 210

...

{'result': {'input': {'location': {'x': -97.881135, 'y': 30.226624}, 'vintage': {'isDefault': True, 'vintageName': 'Census2010_Census2010', 'vintageDescription': 'Census2010 Vintage - Census2010 Benchmark', 'id': '910'}, 'benchmark': {'isDefault': False, 'benchmarkName': 'Public_AR_Census2010', 'benchmarkDescription': 'Public Address Ranges - Census 2010 Benchmark', 'id': '9'}}, 'geographies': {'Census Blocks': [{'BLKGRP': '3', 'UR': '', 'OID': 210403962081896, 'FUNCSTAT': 'S', 'STATE': '48', 'AREAWATER': 0, 'NAME': 'Block 3000', 'SUFFIX': '', 'LSADC': 'BK', 'CENTLON': '-097.8790232', 'HU100': 314, 'LWBLKTYP': 'L', 'BLOCK': '3000', 'BASENAME': '3000', 'INTPTLAT': '+30.2267908', 'POP100': 626, 'MTFCC': 'G5040', 'COUNTY': '453', 'GEOID': '484530017373000', 'CENTLAT': '+30.2267908', 'INTPTLON': '-097.8790232', 'AREALAND': 363486, 'OBJECTID': 9886681, 'TRACT': '001737'}]}}}
getting data for 30.389117-98.002933
{'result': {'input': {'location': {'x': -98.002933, 'y': 30.389117}, 'vintage': 

{'result': {'geographies': {'Census Blocks': [{'BLKGRP': '1', 'UR': '', 'OID': 210403962088809, 'FUNCSTAT': 'S', 'STATE': '48', 'AREAWATER': 1372139, 'NAME': 'Block 1203', 'SUFFIX': '', 'LSADC': 'BK', 'CENTLON': '-098.0084442', 'HU100': 0, 'LWBLKTYP': 'W', 'BLOCK': '1203', 'BASENAME': '1203', 'INTPTLAT': '+30.3811744', 'POP100': 0, 'MTFCC': 'G5040', 'COUNTY': '453', 'GEOID': '484530017801203', 'CENTLAT': '+30.3811744', 'INTPTLON': '-098.0084442', 'AREALAND': 0, 'OBJECTID': 9880813, 'TRACT': '001780'}]}, 'input': {'location': {'x': -98.00591, 'y': 30.386}, 'benchmark': {'benchmarkDescription': 'Public Address Ranges - Census 2010 Benchmark', 'benchmarkName': 'Public_AR_Census2010', 'isDefault': False, 'id': '9'}, 'vintage': {'vintageName': 'Census2010_Census2010', 'vintageDescription': 'Census2010 Vintage - Census2010 Benchmark', 'isDefault': True, 'id': '910'}}}}
getting data for 30.346885-97.746055
{'result': {'input': {'location': {'x': -97.746055, 'y': 30.346885}, 'vintage': {'isDef

{'result': {'input': {'location': {'x': -97.922903, 'y': 30.454699}, 'vintage': {'isDefault': True, 'vintageName': 'Census2010_Census2010', 'vintageDescription': 'Census2010 Vintage - Census2010 Benchmark', 'id': '910'}, 'benchmark': {'isDefault': False, 'benchmarkName': 'Public_AR_Census2010', 'benchmarkDescription': 'Public Address Ranges - Census 2010 Benchmark', 'id': '9'}}, 'geographies': {'Census Blocks': [{'BLKGRP': '2', 'UR': '', 'OID': 210403962092681, 'FUNCSTAT': 'S', 'STATE': '48', 'AREAWATER': 0, 'NAME': 'Block 2069', 'SUFFIX': '', 'LSADC': 'BK', 'CENTLON': '-097.9148790', 'HU100': 133, 'LWBLKTYP': 'L', 'BLOCK': '2069', 'BASENAME': '2069', 'INTPTLAT': '+30.4508945', 'POP100': 217, 'MTFCC': 'G5040', 'COUNTY': '453', 'GEOID': '484530017652069', 'CENTLAT': '+30.4508945', 'INTPTLON': '-097.9148790', 'AREALAND': 1770762, 'OBJECTID': 9889966, 'TRACT': '001765'}]}}}
getting data for 30.078327-97.77888
{'result': {'geographies': {'Census Blocks': [{'BLKGRP': '1', 'UR': '', 'OID': 2

{'result': {'input': {'location': {'x': -97.676687, 'y': 30.448738}, 'vintage': {'isDefault': True, 'vintageName': 'Census2010_Census2010', 'vintageDescription': 'Census2010 Vintage - Census2010 Benchmark', 'id': '910'}, 'benchmark': {'isDefault': False, 'benchmarkName': 'Public_AR_Census2010', 'benchmarkDescription': 'Public Address Ranges - Census 2010 Benchmark', 'id': '9'}}, 'geographies': {'Census Blocks': [{'BLKGRP': '3', 'UR': '', 'OID': 210403962084799, 'FUNCSTAT': 'S', 'STATE': '48', 'AREAWATER': 0, 'NAME': 'Block 3044', 'SUFFIX': '', 'LSADC': 'BK', 'CENTLON': '-097.6767939', 'HU100': 34, 'LWBLKTYP': 'L', 'BLOCK': '3044', 'BASENAME': '3044', 'INTPTLAT': '+30.4485206', 'POP100': 60, 'MTFCC': 'G5040', 'COUNTY': '453', 'GEOID': '484530018513044', 'CENTLAT': '+30.4485206', 'INTPTLON': '-097.6767939', 'AREALAND': 28861, 'OBJECTID': 9877041, 'TRACT': '001851'}]}}}
getting data for 30.366365-97.521337
{'result': {'geographies': {'Census Blocks': [{'BLKGRP': '2', 'UR': '', 'OID': 2104

ConnectionError: ('Connection aborted.', OSError("(10053, 'WSAECONNABORTED')",))

In [ ]:
masterData_df.to_csv(masterData_csv, index=False, header=True)

In [ ]:
######################################################################################  RUN FOR FULL SAMPLE  ###################

# This cell uses us census state fips, county fips, and tract code to access commute times


# Set up list to hold new data
commuteTimeList = []

loopCounter = 0

# Use us census API to get commute time from state, county and tract
for state, county, tract in zip(stateFipsList, countyFipsList ,tractCodeList):
    print("getting data for " + state + county + tract)
    loopCounter += 1
    print(loopCounter)
    targetUrl = "https://api.census.gov/data/2016/acs/acs5/profile?get=DP03_0025E,NAME&for=tract:" + tract + "&in=state:" + state + " county:" + county + "&key=" + census_API_Key
    results = requests.get(targetUrl).json()
    #print(results)
    commuteTimeList.append(results[1][0])

# Add commute time to masterData_df
masterData_df["commuteTime"] = commuteTimeList

# write a CSV
#masterData_df.to_csv(masterData_csv, index=False, header=True)

masterData_df.head()



In [ ]:
######################################################################################  RUN FOR FULL SAMPLE  ###################

# Save to file
DFcsv(masterData_df, "..data/masterData.csv")

In [ ]:
masterData_df.to_csv(masterData_csv, index=False, header=True)

## Heat Mapper

In [ ]:
# Troy's section


gmaps.configure(api_key=google_API_Key)

In [ ]:
# This cell creates a test masterData_df by pulling in Yuta's address file and adds a column as a testm "value to map"
# This cell can be deleted as soon as there is a master data file that includes a property value column or some other value to plot
# The last digit of the zipcode is used as a value that will vary by area and a random number between 0 and 1 is added to create variation in the weights

masterData_df = pd.read_csv(addressList_csv)
zips = masterData_df["zipcode"]
valueToMap = []

for zip in zips:
    lastDigit = zip[-1:]
#    print(last2Digits)
    valueToMap.append(int(lastDigit) + random.uniform(0.0,1.0))
    
masterData_df["valueToMap"] = valueToMap
masterData_df.head()

In [ ]:
# This cell uses gmaps library to create a google heat map from the data in a master data file.
# The masterData csv file is taken as input
# The lat and lon columns are taken as the coordinates for hte heatmap 
# The user specified column is taken as the weighting valies fo each coordinate point

df = masterData_df
columnToMap = 'valueToMap'
max_intensity = df[columnToMap].max()

fig = gmaps.figure()
heatmap_layer = gmaps.heatmap_layer(df[['lat', 'lon']], weights=df[columnToMap], max_intensity=max_intensity, point_radius=10.0)
fig.add_layer(heatmap_layer)
fig

In [ ]:
# this is a function version of the cell above
# the function takes columnToMap as the weights for the points defined by 'lat' and 'lon' columns in the dataframe
# the dataframe can be included as a parameter, if it is not included masterData_df is assumed

def heatMapper(columnToMap, df = masterData_df):
    
    max_intensity = df[columnToMap].max()
    
    fig = gmaps.figure()
    heatmap_layer = gmaps.heatmap_layer(df[['lat', 'lon']], weights=df[columnToMap], max_intensity=max_intensity, point_radius=10.0)
    fig.add_layer(heatmap_layer)

    return;

In [ ]:
heatMapper(columnToMap = 'valueToMap')
fig